In [ ]:
# IMPORTANT: RUN THIS CELL IN ORDER TO IMPORT YOUR KAGGLE DATA SOURCES,
# THEN FEEL FREE TO DELETE THIS CELL.
# NOTE: THIS NOTEBOOK ENVIRONMENT DIFFERS FROM KAGGLE'S PYTHON
# ENVIRONMENT SO THERE MAY BE MISSING LIBRARIES USED BY YOUR
# NOTEBOOK.
import kagglehub
organizations_stanfordu_stanford_question_answering_dataset_path = kagglehub.dataset_download('stanfordu/stanford-question-answering-dataset')

print('Data source import complete.')


100%|██████████| 8.73M/8.73M [00:00<00:00, 81.1MB/s]

Extracting files...


Data source import complete.


In [15]:
print(organizations_stanfordu_stanford_question_answering_dataset_path)

/root/.cache/kagglehub/datasets/stanfordu/stanford-question-answering-dataset/versions/2


In [10]:
import os

# Get the current working directory
current_directory = os.getcwd()

# Print the current working directory
print(f"Current working directory: {current_directory}")

# Print the path to the downloaded dataset
print(f"Downloaded dataset path: {organizations_stanfordu_stanford_question_answering_dataset_path}")

Current working directory: /content
Downloaded dataset path: /root/.cache/kagglehub/datasets/stanfordu/stanford-question-answering-dataset/versions/2


In [3]:
!pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 1.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 3.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.3/44.3 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.3/316.3 kB 8.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 21.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.8/9.8 MB 58.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.9/183.9 kB 16.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 86.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.1/79.1 kB 6.2 MB/s eta 0:00:00
   

In [4]:
!pip install wandb

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥IMPORTING LIBRARIES🔥🔥
</div>


In [5]:
import numpy as np
import pandas as pd
import os
import wandb
import json
import logging
from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

In [6]:
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥Reading Train JSON file🔥🔥
</div>


In [16]:
import os
import json

# Get the downloaded dataset path from the kagglehub output
downloaded_dataset_path = '/root/.cache/kagglehub/datasets/stanfordu/stanford-question-answering-dataset/versions/2'  # Update if needed

# Construct the full file path
file_path = os.path.join(downloaded_dataset_path, 'train-v1.1.json')

# Loading the JSON data from a file
with open(file_path, 'r', encoding='utf-8') as f:
    data = json.load(f)

In [8]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [17]:
# Initialize an empty list to store the converted data
converted_data = []

# Iterate through each item in your data
for item in data['data']:
    # Extract context and QA pairs
    context = item['paragraphs'][0]['context']
    qas = item['paragraphs'][0]['qas']

    # Initialize an empty list to store QA pairs for this context
    qa_list = []

    # Iterate through each QA pair
    for qa in qas:
        # Extract question, answer, answer start position, and ID
        question = qa['question']
        answers = qa['answers']
        if answers:
            answer_text = answers[0]['text']
            answer_start = answers[0]['answer_start']
            qa_id = qa['id']

            # Create a QA dictionary in the desired format
            qa_dict = {
                'id': qa_id,
                'is_impossible': False,  # Assuming all answers are possible in your data
                'question': question,
                'answers': [
                    {
                        'text': answer_text,
                        'answer_start': answer_start,
                    }
                ],
            }

            # Append the QA dictionary to the QA list
            qa_list.append(qa_dict)

    # Create a context dictionary with the QA list
    context_dict = {
        'context': context,
        'qas': qa_list,
    }

    # Append the context dictionary to the converted data list
    converted_data.append(context_dict)

# Print or save the converted data
print(json.dumps(converted_data, indent=4))

[
    {
        "context": "Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend \"Venite Ad Me Omnes\". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.",
        "qas": [
            {
                "id": "5733be284776f41900661182",
                "is_impossible": false,
                "question": "To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?",
                "answers": [
                   

In [18]:
with open('converted_data.json', 'w', encoding='utf-8') as outfile:
     json.dump(converted_data, outfile, indent=4)

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥Reading DEV-JSON file 🔥🔥
</div>


In [20]:
# Loading the Jtrain SON data from a file
with open('/root/.cache/kagglehub/datasets/stanfordu/stanford-question-answering-dataset/versions/2/dev-v1.1.json', 'r', encoding='utf-8') as f:
    test_data = json.load(f)

In [21]:
# Initialize an empty list to store the converted data
converted_data_test = []

# Iterate through each item in your data
for item in data['data']:
    # Extract context and QA pairs
    context = item['paragraphs'][0]['context']
    qas = item['paragraphs'][0]['qas']

    # Initialize an empty list to store QA pairs for this context
    qa_list = []

    # Iterate through each QA pair
    for qa in qas:
        # Extract question, answer, answer start position, and ID
        question = qa['question']
        answers = qa['answers']
        if answers:
            answer_text = answers[0]['text']
            answer_start = answers[0]['answer_start']
            qa_id = qa['id']

            # Create a QA dictionary in the desired format
            qa_dict = {
                'id': qa_id,
                'is_impossible': False,  # Assuming all answers are possible in your data
                'question': question,
                'answers': [
                    {
                        'text': answer_text,
                        'answer_start': answer_start,
                    }
                ],
            }

            # Append the QA dictionary to the QA list
            qa_list.append(qa_dict)

    # Create a context dictionary with the QA list
    context_dict = {
        'context': context,
        'qas': qa_list,
    }

    # Append the context dictionary to the converted data list
    converted_data_test.append(context_dict)

# Print or save the converted data
print(json.dumps(converted_data_test, indent=4))

[
    {
        "context": "Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend \"Venite Ad Me Omnes\". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.",
        "qas": [
            {
                "id": "5733be284776f41900661182",
                "is_impossible": false,
                "question": "To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?",
                "answers": [
                   

In [22]:
import random
import json

# Initialize an empty list to store the converted validation data
converted_validation_data = []

# Randomly sample 100 data samples from eval_data for validation
eval_data_subset = random.sample(converted_data, k=100)

# Iterate through each item in the randomly sampled subset
for item in eval_data_subset:
    # Extract context and QA pairs
    context = item['context']
    qas = item['qas']

    # Initialize an empty list to store QA pairs for this context
    qa_list = []

    # Iterate through each QA pair
    for qa in qas:
        # Extract question, answer, answer start position, and ID
        question = qa['question']
        answers = qa['answers']
        if answers:
            answer_text = answers[0]['text']
            answer_start = answers[0]['answer_start']
            qa_id = qa['id']
            is_impossible = qa['is_impossible']

            # Create a QA dictionary in the desired format
            qa_dict = {
                'id': qa_id,
                'is_impossible': is_impossible,
                'question': question,
                'answers': [
                    {
                        'text': answer_text,
                        'answer_start': answer_start,
                    }
                ],
            }

            # Append the QA dictionary to the QA list
            qa_list.append(qa_dict)

    # Create a context dictionary with the QA list
    context_dict = {
        'context': context,
        'qas': qa_list,
    }

    # Append the context dictionary to the converted validation data list
    converted_validation_data.append(context_dict)

# Convert the converted validation data to JSON format
validation_data = json.dumps(converted_validation_data, ensure_ascii=False, indent=4)

# Print the JSON data
print(validation_data)


[
    {
        "context": "It is on Absecon Island, on the Atlantic coast. Atlantic City was incorporated on May 1, 1854, from portions of Egg Harbor Township and Galloway Township. The city borders Absecon, Brigantine, Pleasantville, Ventnor City and West Atlantic City.",
        "qas": [
            {
                "id": "5706070375f01819005e78a4",
                "is_impossible": false,
                "question": "What is the name of the island on which Atlantic City is located?",
                "answers": [
                    {
                        "text": "Absecon Island",
                        "answer_start": 9
                    }
                ]
            },
            {
                "id": "5706070375f01819005e78a5",
                "is_impossible": false,
                "question": "In what year was Atlantic City incorporated?",
                "answers": [
                    {
                        "text": "1854",
                        "answer_start"

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥Generating Data For Validation🔥🔥
</div>


In [23]:
import random
import json

# Randomly sample 100 data samples from eval_data for validation
eval_data_subset = random.sample(converted_data, k=100)

# Save the randomly sampled validation data to a JSON file
output_file = 'random_validation_data.json'
with open(output_file, 'w', encoding='utf-8') as outfile:
    json.dump(eval_data_subset, outfile, ensure_ascii=False, indent=4)

print(f"Randomly sampled validation data saved to '{output_file}'.")

Randomly sampled validation data saved to 'random_validation_data.json'.


<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥Selecting Model🔥🔥
</div>


In [ ]:
model_type="distilbert"

In [25]:
if model_type == "bert":
    model_name = "bert-base-cased"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "roberta":
    model_name = "roberta-base"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "distilbert":
    model_name = "distilbert-base-cased"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "distilroberta":
    model_type = "roberta"
    model_name = "distilroberta-base"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "electra-base":
    model_type = "electra"
    model_name = "google/electra-base-discriminator"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "electra-small":
    model_type = "electra"
    model_name = "google/electra-small-discriminator"
    print("Your Selected Model Name is : ", model_name)

elif model_type == "xlnet":
    model_name = "xlnet-base-cased"
    print("Your Selected Model Name is : ", model_name)

Your Selected Model Name is :  distilbert-base-cased


<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥GOOGLE-BERT Model Configuration🔥🔥
</div>


In [26]:
wandb.init(project="Question Answer Application")

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: manikanta1010 (manikanta1010-personal) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [27]:
model_args = QuestionAnsweringArgs()
model_args.train_batch_size = 16
model_args.evaluate_during_training = True
model_args.n_best_size = 3
model_args.num_train_epochs = 5

In [28]:
train_args = {
    "reprocess_input_data": True,
    "overwrite_output_dir": True,
    "use_cached_eval_features": True,
    "output_dir": f"outputs/{model_type}",
    "best_model_dir": f"outputs/{model_type}/best_model",
    "evaluate_during_training": True,
    "max_seq_length": 128,
    'num_train_epochs': 100,
    'learning_rate': 1e-5,
    "evaluate_during_training_steps": 1000,
    "wandb_project": "Question Answer Application",
    "wandb_kwargs": {"name": model_name},
    "save_model_every_epoch": False,
    "save_eval_checkpoints": False,
    "n_best_size": 3,
    "train_batch_size": 128,
    "eval_batch_size": 64,
    "use_gpu": True,  # Use GPU for training
    "fp16": True,  # Use mixed-precision training
    "fp16_opt_level": "O1",  # Mixed-precision optimization level
    "gradient_accumulation_steps": 2,  # Accumulate gradients to simulate larger batch size
}

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥GOOGLE-BERT Model Object🔥🔥
</div>


In [29]:
model = QuestionAnsweringModel(
    model_type,model_name, args=train_args,use_cuda=True,
)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/465 [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/263M [00:00<?, ?B/s]

Some weights of DistilBertForQuestionAnswering were not initialized from the model checkpoint at distilbert-base-cased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥GOOGLE-BERT Model Training🔥🔥
</div>


In [ ]:
import torch
from simpletransformers.question_answering import QuestionAnsweringModel
from transformers.data.processors.squad import SquadFeatures # Added this import

# Allow the use of the SquadFeatures class within the 'torch.load' function
torch.serialization.add_safe_globals([SquadFeatures])

model.train_model(converted_data, eval_data='random_validation_data.json') 

add example index and unique id: 100%|██████████| 2596/2596 [00:00<00:00, 805296.44it/s]


Epoch:   0%|          | 0/100 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/question_answering/question_answering_model.py:697: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


Running Epoch 1 of 100:   0%|          | 0/21 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/question_answering/question_answering_model.py:720: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


...

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

Running Epoch 100 of 100:   0%|          | 0/21 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/10 [00:00<?, ?it/s]

(1000,
 {'global_step': [10,
   20,
   30,
   40,
   50,
   60,
   70,
   80,
   90,
   100,
   110,
   120,
   130,
   140,
   150,
   160,
   170,
   180,
   190,
   200,
   210,
   220,
   230,
   240,
   250,
   260,
   270,
   280,
   290,
   300,
   310,
   320,
   330,
   340,
   350,
   360,
   370,
   380,
   390,
   400,
   410,
   420,
   430,
   440,
   450,
   460,
   470,
   480,
   490,
   500,
   510,
   520,
   530,
   540,
   550,
   560,
   570,
   580,
   590,
   600,
   610,
   620,
   630,
   640,
   650,
   660,
   670,
   680,
   690,
   700,
   710,
   720,
   730,
   740,
   750,
   760,
   770,
   780,
   790,
   800,
   810,
   820,
   830,
   840,
   850,
   860,
   870,
   880,
   890,
   900,
   910,
   920,
   930,
   940,
   950,
   960,
   970,
   980,
   990,
   1000,
   1000],
  'correct': [0,
   1,
   3,
   4,
   12,
   6,
   0,
   2,
   10,
   22,
   28,
   31,
   84,
   102,
   125,
   142,
   161,
   177,
   202,
   213,
   226,
   224,
   247,
 

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥Question-Answer||GOOGLE-BERT|| Prediction🔥🔥
</div>


In [32]:
to_predict = [
   {
    "context": "Mistborn is a series of epic fantasy novels written by American author Brandon Sanderson. The first series, published between 2006 and 2008, consists of The Final Empire, The Well of Ascension, and The Hero of Ages.",
    "qas": [
        {
            "id": "00001",
            "question": "Who is the author of the Mistborn series?",
            "answers": [
                {
                    "text": "",
                    "answer_start": -1
                }
            ]
        }
    ]
}
]


In [33]:
model.predict(to_predict=to_predict)

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 5363.56it/s]


Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/question_answering/question_answering_model.py:1348: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


([{'id': '00001',
   'answer': ['epic fantasy',
    'epic fantasy novels written by American author Brandon Sanderson',
    'epic fantasy novels']}],
 [{'id': '00001',
   'probability': [0.3784381103042715, 0.339229729646703, 0.282332031908745]}])

<div style="color:white; background-color:#5642C5; padding: 10px; border-radius: 15px; font-size: 150%; font-family: Verdana; text-align:center; -webkit-text-stroke-width: 1px; -webkit-text-stroke-color: black; text-shadow: 2px 2px 4px rgba(0, 0, 0, 0.7);">
   🔥🔥GOOGLE-BERT Model Saving🔥🔥
</div>


In [34]:
from transformers import QuestionAnsweringPipeline, AutoModelForQuestionAnswering, AutoTokenizer

# Initialize the pipeline
model_checkpoint = f"{model_type}-base-cased"  # Adjust based on your model type
model = AutoModelForQuestionAnswering.from_pretrained(model_checkpoint)
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
qa_pipeline = QuestionAnsweringPipeline(model=model, tokenizer=tokenizer)

# Save the model
output_dir = f"outputs/{model_type}/trained_model"
model.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

# Save the pipeline for later use
qa_pipeline.save_pretrained(output_dir)

print(f"Trained model saved at: {output_dir}")

Some weights of DistilBertForQuestionAnswering were not initialized from the model checkpoint at distilbert-base-cased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Device set to use cuda:0


Trained model saved at: outputs/distilbert/trained_model


In [36]:
'''output_dir = model.args.output_dir

# Save the model using the output directory
model.save_model(output_dir)'''

'output_dir = model.args.output_dir\n\n# Save the model using the output directory\nmodel.save_model(output_dir)'

In [ ]:
import torch
from simpletransformers.question_answering import QuestionAnsweringModel
from transformers import BertTokenizer

# Load the saved model and tokenizer
saved_model_dir = "outputs/bert/trained_model"  # Adjust based on your saved model directory
model = QuestionAnsweringModel("bert", saved_model_dir)

# Create a tokenizer object
tokenizer = BertTokenizer.from_pretrained("bert-base-cased")

# Define the context and question for which you want to generate predictions
context = "Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary."
question = "What is on top of the Main Building?"

# Tokenize the input
inputs = tokenizer(question, context, return_tensors="pt")

# Generate predictions
outputs = model.model(**inputs)

# Decode the predicted answer
answer_start = torch.argmax(outputs.start_logits)
answer_end = torch.argmax(outputs.end_logits) + 1
answer = tokenizer.decode(inputs["input_ids"][0][answer_start:answer_end])

# Print the predicted answer
print("Predicted Answer:", answer)


In [37]:
from google.colab import drive
import os
import shutil

# Mount Google Drive
drive.mount('/content/drive')

# Define the folder path in your Drive
folder_path = '/content/drive/My Drive/MyFolder'  # Replace 'MyFolder' with your desired folder name

# Create the folder if it doesn't exist
if not os.path.exists(folder_path):
  os.makedirs(folder_path)

# Copy the JSON files to the folder
shutil.copy('converted_data.json', folder_path)
shutil.copy('random_validation_data.json', folder_path)

print(f"Files copied to: {folder_path}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Files copied to: /content/drive/My Drive/MyFolder
